In [1]:
import pandas as pd
import numpy as np
import os
import re
import json as js
from pathlib import Path
from tqdm import tqdm
from ast import literal_eval

In [2]:
directory_kamus = "Daftar Kamus Analisis Machine Readable"
directory_kamus_full = "[Full] Daftar Kamus Ekstraksi"

### Algoritma One Entry Corpus ###

In [3]:
POS = ["v","a","n","pron","adv","num","p"]

In [4]:
# Algoritma Tambahan
def is_contain_bold_and_italic(font):
    contains_bold = False; contains_italic = False
    for i in font:
        if "bold" in i.lower(): contains_bold = True
        if "italic" in i.lower(): contains_italic = True
        if contains_bold == True and contains_italic == True: return True
    return False

def is_last_fonem(s): # baru dapat handle fonem (/../) dan ([...])
    if re.match(r'^.*\]$',str(s)): return True
    if re.match(r'^.*\/$',str(s)): return True
    return False

def is_start_fonem(s): # baru dapat handle fonem (/../) dan ([...])
    if re.match(r'^\[.*',str(s)): return True
    if re.match(r'^\/.*',str(s)): return True
    return False

def is_bold_contains_POS(s):
    kata = s.strip()
    
    if len(kata) > 1:
        if is_contain_only_whitespaces(kata[-2]) and (kata[-1] in POS): return True
    else:
        if (kata[-1] in POS): return True
    
    return False

def is_contain_only_whitespaces(s):
    if re.match(r'^\s*$', str(s)): return True
    return False

def is_end_entri(s):
    symbol = [";",",",":"]
    if s in symbol:
        return True
    else:
        return False

In [74]:
# make entry by font
def make_entry_by_font(data):
    result = {
        "Entri":[],
        "entry_font_size_pos":[],
        "posisi_entry":[],
        "page":[]
    }
    
    entry = []; entry_with_font_size_pos = []; pos_dummy = None; page_dummy = None
    
    for ind in data.index:
        txt = data["text"][ind]
        size = data["size"][ind]
        size = round(size,2)
        fnt = data["font"][ind].lower()
        x0 = round(data["x0"][ind],2)
        y0 = round(data["y0"][ind],2)
        x1 = round(data["x1"][ind],2)
        y1 = round(data["y1"][ind],2)
        pos = [x0,y0,x1,y1]
        page = data["page"][ind]
        
        if "bold" in fnt and entry == []: # start entry
            entry.append(txt)
            entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
            pos_dummy = pos
            page_dummy = page
            
        elif "bold" in fnt and entry != []:
            prev_txt = data["text"][ind-1].strip()
            prev_fnt = data["font"][ind-1].lower()
            entry_result = " ".join(entry).strip()
            
            if "bold" in prev_fnt and not txt[0].isdigit() and is_bold_contains_POS(entry_result): # handle prakategorial tanpa koma
                result["Entri"].append(entry_result)
                result["entry_font_size_pos"].append(entry_with_font_size_pos)
                result["posisi_entry"].append(pos_dummy)
                
                if page == page_dummy: 
                    result["page"].append(page_dummy)
                else:
                    result["page"].append([page_dummy,page])
                    
                entry = []; entry_with_font_size_pos = []; pos_dummy = None; page_dummy = None
                entry.append(txt) # mulai entry baru
                entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
                pos_dummy = pos
                page_dummy = page
                
            elif "bold" in prev_fnt and (txt[0].isdigit() or not is_bold_contains_POS(entry_result)): # handle kata bold yang terpisah
                entry.append(txt) 
                entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
                
            elif "bold" not in prev_fnt and (txt[0].isdigit() or is_start_fonem(txt)): # polisemi dan fonem bold
                entry.append(txt) 
                entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
                
            else: 
                result["Entri"].append(entry_result)
                result["entry_font_size_pos"].append(entry_with_font_size_pos)
                result["posisi_entry"].append(pos_dummy)
                
                if page == page_dummy: 
                    result["page"].append(page_dummy)
                else:
                    result["page"].append([page_dummy,page])
                    
                entry = []; entry_with_font_size_pos = []; pos_dummy = None; page_dummy = None
                entry.append(txt) # mulai entry baru
                entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
                pos_dummy = pos
                page_dummy = page
                
        elif "bold" not in fnt.lower() and entry != []:
            entry.append(txt) 
            entry_with_font_size_pos.append([txt,fnt,size,[x0,y0,x1,y1]])
            
        else:
            result["Entri"].append(txt.strip())
            result["entry_font_size_pos"].append([[txt,fnt,size,[x0,y0,x1,y1]]])
            result["posisi_entry"].append(pos)
            result["page"].append(page)
            

    if entry != []: # jika ada entry yang tertinggal
        entry_result = " ".join(entry).strip()
        result["Entri"].append(entry_result)
        result["entry_font_size_pos"].append(entry_with_font_size_pos)
        result["posisi_entry"].append(pos_dummy)
        result["page"].append(page_dummy)

    return result

In [75]:
# algoritma bersihkan entry dari fonem
def clean_entry(data):
    result = {
        "Entri":[],
        "entry_font_size_pos":[],
        "posisi_entry":[],
        "page":[]
    }
    
    for i in range(len(data["Entri"])): # remove fonem
        txt = data["Entri"][i] # data text
        
        if not is_contain_only_whitespaces(txt):
            
            entry_font_size_pos = data["entry_font_size_pos"][i]
            txt = re.sub(r'\[.*?\]',"",txt)
            entry_font_size_pos = clean_entry_font_size_paranthesis(entry_font_size_pos)

            txt = re.sub(r'\/.*?\/',"",txt)
            entry_font_size_pos = clean_entry_font_size_slash(entry_font_size_pos)

            clean = re.sub(' +', ' ', txt) ## remove multiple whitespace
            result["Entri"].append(clean.strip())
            result["entry_font_size_pos"].append(entry_font_size_pos)

            result['posisi_entry'].append(data['posisi_entry'][i])
            result['page'].append(data['page'][i])
    
    for j in range(1,len(result['Entri'])): # fix symbol
        array_simbol = []; array_simbol_font_size_pos = []
        
        prev_txt_split = result["Entri"][j-1].split(" ")
        prev_entri_font_size_pos = result['entry_font_size_pos'][j-1]
        
        # buang seluruh simbol, kecuali ; pada entri sebelumnya
        while (prev_txt_split[-1] != "") and (not is_end_entri(prev_txt_split[-1][-1])):
            if (prev_txt_split[-1][0].isalnum()) or (prev_txt_split[-1][-1].isalnum()): 
                break
                
            else:
                if (prev_txt_split==[] or prev_entri_font_size_pos == []):break
                
                array_simbol.append(prev_txt_split[-1])
                array_simbol_font_size_pos.append(prev_entri_font_size_pos[-1])
                del prev_txt_split[-1]
                del prev_entri_font_size_pos[-1]
                
                result["Entri"][j-1] = " ".join(prev_txt_split)
                result['entry_font_size_pos'][j-1] = prev_entri_font_size_pos
            
            if (prev_txt_split==[] or prev_entri_font_size_pos == []):break
        
        txt_split = result['Entri'][j].split(" ")
        if is_end_entri(txt_split[0]): 
            result['Entri'][j-1] = result['Entri'][j-1] + txt_split[0]
            result['entry_font_size_pos'][j-1].append(result['entry_font_size_pos'][j][0])
            
            del txt_split[0]
            result['entry_font_size_pos'][j] = result['entry_font_size_pos'][j][1:]
            result['Entri'][j] = " ".join(txt_split)
        
        if array_simbol != []:
            new_entry = []
            new_entry.extend(array_simbol)
            new_entry.extend(txt_split)
            result['Entri'][j] = " ".join(new_entry)
            
            new_entry_font_size_pos = []
            new_entry_font_size_pos.extend(array_simbol_font_size_pos)
            new_entry_font_size_pos.extend(result['entry_font_size_pos'][j])
            result['entry_font_size_pos'][j] = new_entry_font_size_pos    
    
    for l in range(len(result['entry_font_size_pos'])):
        if result['entry_font_size_pos'][l] != []:
            result['posisi_entry'][l] = result['entry_font_size_pos'][l][0][-1]
        
    return result

In [76]:
def clean_entry_font_size_paranthesis(data):
    clean_data = []
    i = 0
    
    while i < len(data):
        txt = data[i][0]
        if re.match(r'^.*\[.*?\].*$',str(txt)): ## kasus ...[..]...
            clean = re.sub(r'\[.*?\]',"",txt)
            if clean == "":
                i += 1
            else:
                clean_data.append([clean.strip(),data[i][1],data[i][2],data[i][3]])
                i += 1
        elif re.match(r'^.*\[.*',str(txt)): ## kasus ...[...
            nxt = i+1
            if nxt > len(data)-1: # i di indeks terakhir
                clean_data.append(data[i])
                break
                
            nxt_txt = data[nxt][0]
            while not re.match(r'^.*\].*$',str(nxt_txt)): # mencari "...]...."
                nxt += 1
                if nxt > len(data)-1: break
                nxt_txt = data[nxt][0]
            
            if nxt > len(data)-1: # jika "....]..." tidak ditemukan
                for k in range(i,nxt):
                    clean_data.append(data[k])
                break
            else:
                ## append [ pertama
                clean = txt.split("[",1)[0]
                if clean != "":
                    clean_data.append([clean.strip(),data[i][1],data[i][2],data[i][3]])
                    
                ## append ] kedua
                clean_nxt = nxt_txt.split("]",1)[1]
                if clean_nxt != "":
                    clean_data.append([clean_nxt.strip(),data[nxt][1],data[nxt][2],data[i][3]])
                
                i = nxt+1
        else:
            clean_data.append(data[i])
            i += 1
    
    return clean_data


def clean_entry_font_size_slash(data):
    clean_data = []
    i = 0
    
    while i < len(data):
        txt = data[i][0]
        if re.match(r'^.*\/.*?\/.*$',str(txt)): ## kasus .../../...
            clean = re.sub(r'\/.*?\/',"",txt)
            if clean == "":
                i += 1
            else:
                clean_data.append([clean.strip(),data[i][1],data[i][2],data[i][3]])
                i += 1
        elif re.match(r'^.*\/.*',str(txt)): ## kasus .../...
            nxt = i+1
            if nxt > len(data)-1: # i di indeks terakhir
                clean_data.append(data[i])
                break
                
            nxt_txt = data[nxt][0]
            while not re.match(r'^.*\/.*$',str(nxt_txt)): # mencari ".../...."
                nxt += 1
                if nxt > len(data)-1: break
                nxt_txt = data[nxt][0]
            
            if nxt > len(data)-1: # jika "..../..." tidak ditemukan
                for k in range(i,nxt):
                    clean_data.append(data[k])
                break
            else:
                ## append / pertama
                clean = txt.split("/",1)[0]
                if clean != "":
                    clean_data.append([clean.strip(),data[i][1],data[i][2],data[i][3]])
                    
                ## append / kedua
                clean_nxt = nxt_txt.split("/",1)[1]
                if clean_nxt != "":
                    clean_data.append([clean_nxt.strip(),data[nxt][1],data[nxt][2],data[i][3]])
                
                i = nxt+1
        else:
            clean_data.append(data[i])
            i += 1
    
    return clean_data

In [77]:
def fix_page(pages):
    clean_page = []
    cnt = 1;
    
    for i in range(len(pages)):
        if i == 0:
            clean_page.append(cnt)
        else:
            if isinstance(pages[i], list):
                clean_page.append([cnt,cnt+1])
                cnt += 1
            else:
                if isinstance(pages[i-1], list):
                    clean_page.append(cnt)
                else:
                    if pages[i] == pages[i-1]:
                        clean_page.append(cnt)
                    else:
                        cnt += 1
                        clean_page.append(cnt)
    return clean_page

In [79]:
# memisahkan prakategorial
def seperate_prakategorial(data):
    result = {
        "Entri":[],
        "entry_font_size_pos":[],
        "posisi_entry":[],
        "page":[]
    }
    
    for i in range(len(data["Entri"])):
        txt = data["Entri"][i]
        split_txt = txt.strip().split(",",1)
        
        if len(split_txt) < 2 or txt[-1] == ",": # tidak terdapat koma atau koma berada di akhir
            result['Entri'].append(txt)
            result['entry_font_size_pos'].append(data['entry_font_size_pos'][i])
            result['page'].append(data['page'][i])
            result['posisi_entry'].append(data['posisi_entry'][i])
        
        else:
            frst_entri = split_txt[0].strip().split(" ")
            sec_entri = split_txt[1].strip().split(" ")
            
            for j in range(len(frst_entri)):
                frst_entri[j] = frst_entri[j].strip()
            
            for k in range(len(sec_entri)):
                sec_entri[k] = sec_entri[k].strip()
                
            if len(frst_entri) <= 2 and (frst_entri[0] == "" or frst_entri[0] == ","): # koma berada di awal entri
                result['Entri'].append(txt)
                result['entry_font_size_pos'].append(data['entry_font_size_pos'][i])
                result['page'].append(data['page'][i])
                result['posisi_entry'].append(data['posisi_entry'][i])
            
            else:
                inf_frst_entri = data['entry_font_size_pos'][i][:len(frst_entri)]
                
                if "bold" in inf_frst_entri[-1][1].lower() or frst_entri[-1] in POS:
                    if (len(frst_entri) + len(sec_entri)) == len(data['entry_font_size_pos'][i]): # kasus koma menempel
                        frst_entri[-1] = frst_entri[-1] + ","
                        inf_sec_entri = data['entry_font_size_pos'][i][len(frst_entri):]

                    else: # kasus koma tidak menempel
                        frst_entri.append(",")
                        inf_frst_entri = data['entry_font_size_pos'][i][:len(frst_entri)+1]
                        inf_sec_entri = data['entry_font_size_pos'][i][len(frst_entri)+1:]
                        
                    # entri pertama
                    result['Entri'].append(" ".join(frst_entri))
                    result['entry_font_size_pos'].append(inf_frst_entri)
                    result['page'].append(data['page'][i])
                    result['posisi_entry'].append(data['posisi_entry'][i])

                    # entri kedua
                    result['Entri'].append(" ".join(sec_entri))
                    result['entry_font_size_pos'].append(inf_sec_entri)
                    result['page'].append(data['page'][i])
                    result['posisi_entry'].append(data['posisi_entry'][i])

                else:
                    result['Entri'].append(txt)
                    result['entry_font_size_pos'].append(data['entry_font_size_pos'][i])
                    result['page'].append(data['page'][i])
                    result['posisi_entry'].append(data['posisi_entry'][i])
                
                
    return result

In [80]:
def categorize_prakategorial(entries):
    output = []
    
    for i in entries:
        txt_split = i.split(" ")
        if i == "" or len(i)==1:
            output.append(0)
        else:
            if re.match(r'.*\,$',str(i)) and len(txt_split) <= 3: 
                output.append(1)
            elif is_contain_only_whitespaces(i[-2]) and (i[-1] in POS):
                output.append(1)
            else:
                output.append(0)
    return output

In [81]:
def build_corpus_one_entry_by_font(data):
    # tahapan awal, pendekatan dengan font
    result = make_entry_by_font(data)
    clean_result = clean_entry(result)
    clean_result = seperate_prakategorial(clean_result)
    clean_result["is_padanan_lema"] = categorize_prakategorial(clean_result["Entri"])
    clean_result["page"] = fix_page(clean_result["page"])
    
    return clean_result

### Main Program

In [85]:
# ganti directory
directory_CSV = "CSV JSON all information"
directory_hasil = "CSV One Entry JSON With Font Approach"

for filename in tqdm(os.listdir(directory_CSV)):
    data = pd.read_csv(directory_CSV + "/" + filename)
    data = data.dropna()
    data = data.reset_index(drop=True)
    input_fonts = data["font"].values.tolist()
    new_filename = os.path.splitext(filename)[0]
    
    if is_contain_bold_and_italic(input_fonts):
        print("====" + new_filename + "====")
        CSV_res = build_corpus_one_entry_by_font(data)

        result_csv = pd.DataFrame.from_dict(CSV_res)
        result_csv = result_csv.reset_index(drop=True)
        
        result_csv = result_csv.dropna()
        result_csv = result_csv.reset_index(drop=True)
        
        result_csv.to_csv(directory_hasil + "/" + new_filename + "-one_entry_from_JSON-font.csv",index=False)

 22%|██████████████████▋                                                                 | 2/9 [00:00<00:00, 13.44it/s]

====41. Kamus Bahasa Indonesia-Bali A-K (1997)-page_58_59-hasil-ekstraksi====
====43. Kamus Bahasa Indonesia-Bahasa Minangkabau I (1994)-page_23_24-hasil-ekstraksi====
====54. Kamus Bahasa Indonesia Mentawai (1998)-page_23_24-hasil-ekstraksi====
====57. Kamus Bahasa Bugis-Indonesia (1977)-page_20_21-hasil-ekstraksi====


 67%|████████████████████████████████████████████████████████                            | 6/9 [00:00<00:00, 12.83it/s]

====61. Kamus Banjar-Indonesia (1977)-page_51_52-hasil-ekstraksi====
====68. Kamus Dwibahasa Bahasa Talaud - Bahasa Indonesia (2018)-page_19_20-hasil-ekstraksi====
====77. Kamus Samawa-Indonesia Edisi 2 (2017)-page_27_28-hasil-ekstraksi====


 89%|██████████████████████████████████████████████████████████████████████████▋         | 8/9 [00:00<00:00,  9.51it/s]

====89. Kamus Dwibahasa Bahasa Mooi-Bahasa Indonesia (2017)-page_17_18-hasil-ekstraksi====


100%|████████████████████████████████████████████████████████████████████████████████████| 9/9 [00:00<00:00, 10.61it/s]

====91. Kamus Simalungun - Indonesia (edisi kedua) (2015)-page_48_49-hasil-ekstraksi====


In [86]:
directory_hasil = "CSV One Entry JSON With Font Approach"

# drop null data 
for filename in tqdm(os.listdir(directory_hasil)):
    data_clean = pd.read_csv(directory_hasil + "/" + filename)
    data_clean = data_clean.dropna()
    data_clean = data_clean[data_clean["entry_font_size_pos"] != "[]"]
    data_clean = data_clean.reset_index(drop=True)
    
    data_clean.to_csv(directory_hasil + "/" + filename,index=False)

100%|████████████████████████████████████████████████████████████████████████████████████| 9/9 [00:00<00:00, 84.38it/s]


### Main Program Kamus Full (JSON)

In [87]:
directory_CSV = "[Full] CSV JSON all information - Final"
directory_hasil = "[Full] CSV One Entry JSON With Font Approach"

for filename in tqdm(os.listdir(directory_CSV)):
    data = pd.read_csv(directory_CSV + "/" + filename)
    
    data = data.dropna()
    data = data.reset_index(drop=True)
    
    input_fonts = data["font"].values.tolist()
    new_filename = os.path.splitext(filename)[0]
    
    if is_contain_bold_and_italic(input_fonts):
        print("====" + new_filename + "====")
        CSV_res = build_corpus_one_entry_by_font(data)
        
        result_csv = pd.DataFrame.from_dict(CSV_res)
        result_csv = result_csv[result_csv["Entri"] != ""]
        result_csv = result_csv[result_csv["entry_font_size_pos"] != "[]"]
        result_csv = result_csv.reset_index(drop=True)

        result_csv = pd.DataFrame.from_dict(CSV_res)
        result_csv.to_csv(directory_hasil + "/" + new_filename + "-one_entry_from_JSON-font.csv",index=False)

  0%|                                                                                           | 0/47 [00:00<?, ?it/s]

====10. Kamus Bahasa Indonesia-Dayak Deah Edisi I (2013)-hasil-ekstraksi====


  2%|█▊                                                                                 | 1/47 [00:06<04:39,  6.07s/it]

====12. Kamus Bahasa Indonesia-Kaidipang L-Z (2000)-hasil-ekstraksi====


  4%|███▌                                                                               | 2/47 [00:19<07:57, 10.62s/it]

...

 96%|██████████████████████████████████████████████████████████████████████████████▌   | 45/47 [05:29<00:12,  6.07s/it]

====9. Kamus Manado-Indonesia (1985)-hasil-ekstraksi====


 98%|████████████████████████████████████████████████████████████████████████████████▎ | 46/47 [05:33<00:05,  5.57s/it]

====91. Kamus Simalungun - Indonesia (edisi kedua) (2015)-hasil-ekstraksi====


100%|██████████████████████████████████████████████████████████████████████████████████| 47/47 [05:44<00:00,  7.34s/it]


In [88]:
directory_hasil = "[Full] CSV One Entry JSON With Font Approach"

for filename in tqdm(os.listdir(directory_hasil)):
    data_clean = pd.read_csv(directory_hasil + "/" + filename)
    data_clean = data_clean.dropna()
    data_clean = data_clean[data_clean["entry_font_size_pos"] != "[]"]
    data_clean = data_clean.reset_index(drop=True)
    
    data_clean.to_csv(directory_hasil + "/" + filename,index=False)

100%|██████████████████████████████████████████████████████████████████████████████████| 48/48 [00:09<00:00,  5.26it/s]


### Main Program (XML) ###

In [9]:
directory_CSV = "CSV XML All Information"
directory_hasil = "CSV One Entry XML With Font Approach"

for filename in tqdm(os.listdir(directory_CSV)):
    data = pd.read_csv(directory_CSV + "/" + filename)
    data.rename(columns={"kata":"text"},inplace=True)
    data = data.dropna()
    data = data.reset_index(drop=True)
    input_fonts = data["font"].values.tolist()
    new_filename = os.path.splitext(filename)[0]
    
    if is_contain_bold_and_italic(input_fonts):
        print("====" + new_filename + "====")
        CSV_res = build_corpus_one_entry_by_font(data)

        result_csv = pd.DataFrame.from_dict(CSV_res)
        result_csv.to_csv(directory_hasil + "/" + new_filename + "-one_entry_from_XML.csv",index=False)
#         try:
#             CSV_res = build_corpus_one_entry_by_font(data)

#             result_csv = pd.DataFrame.from_dict(CSV_res)
#             result_csv.to_csv(directory_hasil + "/" + new_filename + "-one_entry_from_XML.csv",index=False)
#         except:
#             print("==== Kamus Gagal ====")
#             print(new_filename)

 17%|█████████████▊                                                                     | 3/18 [00:00<00:00, 42.85it/s]

====41. Kamus Bahasa Indonesia-Bali A-K (1997)-page_58_59_kata====


KeyError: 'size'

### Cek Kamus ###

In [23]:
kamus = pd.read_csv("coba 89-one_entry_from_JSON-font.csv")

In [24]:
kamus = kamus.dropna()
kamus = kamus[kamus["entry_font_size_pos"] != "[]"]

In [25]:
entry_font_size_pos = []

for i in kamus["entry_font_size_pos"].values.tolist():
    entry_font_size_pos.append(literal_eval(i))

In [26]:
# tampilkan seluruh baris dan seluruh nilai pada kolom
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

display(kamus)

# reset option
pd.reset_option("display")

Entri  \
0                                                                                                                                                                                                                           1   
1                                                                                                                                                                    A aba n bete; talas: nja aba dun trung ibu membakar bete   
2                                                                                                                                            abletsing a terbalik: nemot amblemba king on abletsing dia memakai baju terbalik   
3                                                                                                                                                              abusi n kakek: kandei abusi mse ket ong kakek saya masih hidup   
4                                                                                                                                                       agha n kakak; abang: nggo syoli kandei agha orang itu itu kakak saya;   
5                                                                                                                  agha kambung n kakak perempuan: kandei agha kambung syoli mbei ati awum kakak perempuan saya sudah menikah   
6                                                                                                                                  agrog-agrog v putar, memutari: nemot gereja yap kanding agrog-agrog mereka memutari gereja   
7                                                                                                                                                      agrok amtung a pusing: kat yegembu agrok amtung kepalaku terasa pusing   
8                                                                                                                                                                     ai n bapak: kat ai nmo su Markus nama bapak saya Markus   
9                                                                                                                                                            alei n akal; pikiran: snou nak nmon alei manusia mempunyai akal;   
10                                                                                                                alei alaptung n angan-angan; cita- cita: kanei alei alaptung guru se ablei aru cita-cita adik menjadi guru;   
11                                                                                                                                  alei dungdung v anggapan: alei dungdung nggo ale kba sumbui anggapan itu tidak masuk akal   
12                                                                                                                                                                       aleikba a bodoh: nggo donak aleikba anak itu bodoh 2   
13                                                                                                                                       alem n tanjung: nemot alem bro se manei kasim nemtong mereka mencari ikan di tanjung   
14                                                                                         alen n bambu untuk memotong (pisau pada zaman dahulu): nja alen de mbiok kendeng tumbu trung ibu memotong daging babi dengan bambu   
15                                                                                                                       aleng a 1 bengkok: nggo di aleng kayu itu bengkok; 2 miring: nggo kutum aleng atung tiang itu miring   
16                                                                                                                                                                     ali 1 a berat: nje kemba ali nale tas ini sangat berat   
17                                                                                                                                                                    